In [ ]:
import json
import pandas as pd

# Path to the uploaded .jsonl file
file_path = '' #@param {type:'string'}

# Initialize lists to store data
data = []

# Read the .jsonl file line by line
with open(file_path, 'r') as file:
    for line in file:
        try:
            # Parse each line as a JSON object
            json_obj = json.loads(line.strip())
            data.append(json_obj)
        except json.JSONDecodeError as e:
            print(f"Error decoding JSON line: {e}")
            continue

# Convert the list of JSON objects to a Pandas DataFrame for easier exploration
df = pd.DataFrame(data)

# Display basic information about the DataFrame
print("=== File Overview ===")
print(f"Number of records: {len(df)}")
print("\nColumn names:")
print(df.columns.tolist())
print("\nData types:")
print(df.dtypes)

# Display the first few rows
print("\n=== First 5 Rows ===")
print(df.head())

# Display basic statistics
print("\n=== Basic Statistics ===")
print(df.describe(include='all'))

# Check for missing values
print("\n=== Missing Values ===")
print(df.isnull().sum())

# Optional: Display unique values in each column
print("\n=== Unique Values per Column ===")
for col in df.columns:
    print(f"{col}: {df[col].nunique()} unique values")

In [ ]:
import json
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from collections import Counter
import numpy as np

# Set up plotting style
plt.style.use('default')
%matplotlib inline

# Path to the uploaded .jsonl file
#file_path = ''

# Read the .jsonl file into a DataFrame
data = []
with open(file_path, 'r') as file:
    for line in file:
        try:
            json_obj = json.loads(line.strip())
            data.append(json_obj)
        except json.JSONDecodeError as e:
            print(f"Error decoding JSON line: {e}")
            continue
df = pd.DataFrame(data)

# 1. Rating Distribution
print("=== Rating Distribution ===")
rating_counts = df['rating'].value_counts()
plt.figure(figsize=(8, 5))
sns.barplot(x=rating_counts.index, y=rating_counts.values)
plt.title('Distribution of Image Ratings')
plt.xlabel('Rating')
plt.ylabel('Count')
plt.show()
print(rating_counts)

# 2. Tag Analysis
print("\n=== Top 10 Most Common Tags ===")
# Combine all tags into a single list
all_tags = []
for tags in df['tag_string'].dropna():
    all_tags.extend(tags.split())
tag_counts = Counter(all_tags)
top_tags = pd.DataFrame(tag_counts.most_common(10), columns=['Tag', 'Count'])
plt.figure(figsize=(10, 6))
sns.barplot(x='Count', y='Tag', data=top_tags)
plt.title('Top 10 Most Common Tags')
plt.show()
print(top_tags)

# 3. Image Dimensions Analysis
print("\n=== Image Dimensions Analysis ===")
plt.figure(figsize=(10, 6))
plt.scatter(df['image_width'], df['image_height'], alpha=0.5, s=50)
plt.title('Image Width vs. Height')
plt.xlabel('Width (pixels)')
plt.ylabel('Height (pixels)')
plt.xscale('log')
plt.yscale('log')
plt.grid(True)
plt.show()
print(f"Median Width: {df['image_width'].median()}")
print(f"Median Height: {df['image_height'].median()}")
print(f"Aspect Ratio (Width/Height) Stats:\n{df['image_width'].div(df['image_height']).describe()}")

# 4. Score and Voting Analysis
print("\n=== Score and Voting Analysis ===")
plt.figure(figsize=(10, 6))
sns.histplot(df['score'], bins=30, kde=True)
plt.title('Distribution of Image Scores')
plt.xlabel('Score')
plt.ylabel('Count')
plt.show()
print(f"Score Stats:\n{df['score'].describe()}")
print(f"\nCorrelation between Up Score and Down Score: {df['up_score'].corr(df['down_score'])}")

# 5. Summary Length Analysis
print("\n=== Summary Length Analysis ===")
df['summary_length'] = df['regular_summary'].dropna().apply(lambda x: len(str(x).split()))
plt.figure(figsize=(10, 6))
sns.histplot(df['summary_length'], bins=30, kde=True)
plt.title('Distribution of Regular Summary Word Counts')
plt.xlabel('Word Count')
plt.ylabel('Count')
plt.show()
print(f"Summary Length Stats:\n{df['summary_length'].describe()}")

# 6. Missing Data Heatmap
print("\n=== Missing Data Heatmap ===")
plt.figure(figsize=(12, 8))
sns.heatmap(df.isnull(), cbar=False, cmap='viridis')
plt.title('Missing Data Heatmap')
plt.show()

# 7. Source Platform Analysis
print("\n=== Source Platform Analysis ===")
# Extract domain from source URLs
df['source_domain'] = df['source'].dropna().str.extract(r'(https?://[^/]+)')
source_counts = df['source_domain'].value_counts().head(10)
plt.figure(figsize=(10, 6))
sns.barplot(x=source_counts.values, y=source_counts.index)
plt.title('Top 10 Source Domains')
plt.xlabel('Count')
plt.ylabel('Domain')
plt.show()
print(source_counts)

# 8. File Size vs. Image Dimensions
print("\n=== File Size vs. Image Dimensions ===")
plt.figure(figsize=(10, 6))
plt.scatter(df['image_width'] * df['image_height'], df['file_size'], alpha=0.5)
plt.title('File Size vs. Image Area')
plt.xlabel('Image Area (Width * Height)')
plt.ylabel('File Size (bytes)')
plt.xscale('log')
plt.yscale('log')
plt.grid(True)
plt.show()
print(f"Correlation between Image Area and File Size: {df['file_size'].corr(df['image_width'] * df['image_height'])}")

In [ ]:
import json
import pandas as pd

# Path to the uploaded .jsonl file
#file_path = ''

# Read the .jsonl file into a DataFrame
data = []
with open(file_path, 'r') as file:
    for line in file:
        try:
            json_obj = json.loads(line.strip())
            data.append(json_obj)
        except json.JSONDecodeError as e:
            print(f"Error decoding JSON line: {e}")
            continue
df = pd.DataFrame(data)

# Define columns that likely contain prompts/image descriptions
description_columns = [
    'regular_summary',
    'individual_parts',
    'midjourney_style_summary',
    'deviantart_commission_request',
    'brief_summary'
]

# Initialize a list to store all descriptions
all_descriptions = []

# Iterate through each row and collect non-empty descriptions
for index, row in df.iterrows():
    record_descriptions = []
    for col in description_columns:
        if pd.notnull(row[col]) and row[col]:  # Check for non-null and non-empty values
            record_descriptions.append(f"{col}: {row[col]}")
    if record_descriptions:
        all_descriptions.append({
            'id': row['id'],
            'descriptions': record_descriptions
        })

# Display all descriptions
print(f"=== All Prompts/Image Descriptions (Total Records with Descriptions: {len(all_descriptions)}) ===")
for entry in all_descriptions:
    print(f"\nImage ID: {entry['id']}")
    for desc in entry['descriptions']:
        print(f"  {desc}")
    print("-" * 80)

# Optional: Save descriptions to a text file for easier review
with open('/content/image_descriptions.txt', 'w') as f:
    f.write(f"Total Records with Descriptions: {len(all_descriptions)}\n\n")
    for entry in all_descriptions:
        f.write(f"Image ID: {entry['id']}\n")
        for desc in entry['descriptions']:
            f.write(f"  {desc}\n")
        f.write("-" * 80 + "\n")

print("\nDescriptions have been saved to '/content/image_descriptions.txt'.")

In [ ]:
import json,os
import pandas as pd

# Path to the uploaded .jsonl file
file_path = '' #@param {type:'string'}

# Read the .jsonl file into a DataFrame
data = []
with open(file_path, 'r') as file:
    for line in file:
        try:
            json_obj = json.loads(line.strip())
            data.append(json_obj)
        except json.JSONDecodeError as e:
            print(f"Error decoding JSON line: {e}")
            continue
df = pd.DataFrame(data)

# Define columns that likely contain prompts/image descriptions
description_columns = [
    'regular_summary',
    'individual_parts',
    'midjourney_style_summary',
    'deviantart_commission_request',
    'brief_summary'
]

# Initialize a list to store all descriptions
all_descriptions = []

# Iterate through each row and collect non-empty descriptions
for index, row in df.iterrows():
    record_descriptions = []
    for col in description_columns:
        if pd.notnull(row[col]) and row[col]:  # Check for non-null and non-empty values
            record_descriptions.append(f"{col}: {row[col]}")
    if record_descriptions:
        all_descriptions.append({
            'id': row['id'],
            'descriptions': '; '.join(record_descriptions)  # Join descriptions with semicolon
        })

# Convert to DataFrame for Parquet
output_df = pd.DataFrame(all_descriptions)

# Save to Parquet file
output_path = '' #@param {type:'string'}
output_df.to_parquet(output_path, index=False)
os.remove(f'{file_path}')
print(f"\nDescriptions have been saved to '{output_path}'.")